# Outlines 
#### 1. Data cleaning 
#### 2. feature engineering 
#### 3. Getting more insights 
#### 4. Data Pre-processing
      - Splitting  
      - fearure transformation 
#### 5. modeling 
#### 6. evalution 

In [223]:
#load libraries
import pandas as pd
import numpy as np
import seaborn as sns
import time
import random
import plotly.express as px
import matplotlib.pyplot as plt
import plotly.figure_factory as ff
from iso639 import languages
import user_agents
from ip2geotools.databases.noncommercial import DbIpCity as ip2geo
import requests
import json
from geopy.distance import great_circle
from geopy.geocoders import Nominatim
from datasist.structdata import detect_outliers
from sklearn.impute import SimpleImputer
from sklearn.impute import KNNImputer
from sklearn.preprocessing import OneHotEncoder
import category_encoders as ce
from datetime import datetime
from sklearn.model_selection import train_test_split
from imblearn.under_sampling import RandomUnderSampler
from imblearn.over_sampling import SMOTE
from imblearn.over_sampling import RandomOverSampler 
from imblearn.pipeline import Pipeline
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.linear_model import LinearRegression
from sklearn import metrics
from sklearn.linear_model import Ridge
from sklearn.tree import DecisionTreeRegressor
from sklearn.tree import plot_tree
from sklearn.ensemble import RandomForestRegressor
%matplotlib inline
# Standard figure size for all 
sns.set(rc={'figure.figsize': [7, 7]}, font_scale=1.2) 

In [224]:
#import data
df=pd.read_csv('.//Data//train.csv')
df.head()
df.sample(5)

Name    Location  Year  \
5834   Toyota Innova 2.5 G (Diesel) 8 Seater      Jaipur  2013   
4966  Toyota Innova 2.5 VX (Diesel) 8 Seater      Mumbai  2014   
131               Mahindra XUV500 AT W10 FWD      Jaipur  2016   
5376     Hyundai Verna 1.6 CRDI AT SX Option  Coimbatore  2017   
3744                     Maruti Alto 800 LXI   Hyderabad  2015   

      Kilometers_Driven Fuel_Type Transmission Owner_Type     Mileage  \
5834             250000    Diesel       Manual     Second  12.99 kmpl   
4966              87143    Diesel       Manual      First  12.99 kmpl   
131               54000    Diesel    Automatic      First   16.0 kmpl   
5376              36931    Diesel    Automatic      First  19.08 kmpl   
3744              24617    Petrol       Manual      First  22.74 kmpl   

       Engine      Power  Seats New_Price  Price  
5834  2494 CC  100.6 bhp    8.0       NaN   7.90  
4966  2494 CC    100 bhp    8.0       NaN  12.50  
131   2179 CC    140 bhp    7.0       NaN  13.25  
5376  1582 CC  126.2 bhp    5.0       NaN   9.48  
3744   796 CC   47.3 bhp    5.0       NaN   2.36

# 1. Data cleaning 


### 1.1 Investegation 

In [225]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6019 entries, 0 to 6018
Data columns (total 13 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   Name               6019 non-null   object 
 1   Location           6019 non-null   object 
 2   Year               6019 non-null   int64  
 3   Kilometers_Driven  6019 non-null   int64  
 4   Fuel_Type          6019 non-null   object 
 5   Transmission       6019 non-null   object 
 6   Owner_Type         6019 non-null   object 
 7   Mileage            6017 non-null   object 
 8   Engine             5983 non-null   object 
 9   Power              5983 non-null   object 
 10  Seats              5977 non-null   float64
 11  New_Price          824 non-null    object 
 12  Price              6019 non-null   float64
dtypes: float64(2), int64(2), object(9)
memory usage: 611.4+ KB


In [226]:
df.describe()
df.describe(include='O')
df.describe(include='all')

Name Location         Year  Kilometers_Driven  \
count                     6019     6019  6019.000000       6.019000e+03   
unique                    1876       11          NaN                NaN   
top     Mahindra XUV500 W8 2WD   Mumbai          NaN                NaN   
freq                        49      790          NaN                NaN   
mean                       NaN      NaN  2013.358199       5.873838e+04   
std                        NaN      NaN     3.269742       9.126884e+04   
min                        NaN      NaN  1998.000000       1.710000e+02   
25%                        NaN      NaN  2011.000000       3.400000e+04   
50%                        NaN      NaN  2014.000000       5.300000e+04   
75%                        NaN      NaN  2016.000000       7.300000e+04   
max                        NaN      NaN  2019.000000       6.500000e+06   

       Fuel_Type Transmission Owner_Type    Mileage   Engine   Power  \
count       6019         6019       6019       6017     5983    5983   
unique         5            2          4        442      146     372   
top       Diesel       Manual      First  18.9 kmpl  1197 CC  74 bhp   
freq        3205         4299       4929        172      606     235   
mean         NaN          NaN        NaN        NaN      NaN     NaN   
std          NaN          NaN        NaN        NaN      NaN     NaN   
min          NaN          NaN        NaN        NaN      NaN     NaN   
25%          NaN          NaN        NaN        NaN      NaN     NaN   
50%          NaN          NaN        NaN        NaN      NaN     NaN   
75%          NaN          NaN        NaN        NaN      NaN     NaN   
max          NaN          NaN        NaN        NaN      NaN     NaN   

              Seats   New_Price        Price  
count   5977.000000         824  6019.000000  
unique          NaN         540          NaN  
top             NaN  95.13 Lakh          NaN  
freq            NaN           6          NaN  
mean       5.278735         NaN     9.479468  
std        0.808840         NaN    11.187917  
min        0.000000         NaN     0.440000  
25%        5.000000         NaN     3.500000  
50%        5.000000         NaN     5.640000  
75%        5.000000         NaN     9.950000  
max       10.000000         NaN   160.000000

In [227]:
df.shape
df.dtypes
df.isna().sum()
df.isna().sum()/len(df) * 100
df.isna().sum()/df.shape[0] * 100
df.isna().mean() * 100
df.duplicated().sum()

0

#### Notes 
- Numerical values mixed with text in (Mileage, Engine, Power) columns. 
    - in Milage column we have 2 units (kmpl & km/kg)
- Most of New_Price Column is null values (so, we have 2 solution.) 
    - remove it or scrap some data to fill it. 
- Null values values in other columns 
- Seats columns have some values with Zero !! 
- duplicated rows founded 
- Power column have values "null bhp" 

###  1.2 Working with data issues 

> Dropping duplicated columns 

In [228]:
#drop duplicates
#df.drop_duplicates(inplace=True,reset_index=True)
df.drop_duplicates(inplace=True)

> Drop "New_Price" column because most of them is null 


In [229]:
#drop unnecassary column
df.drop('New_Price',axis=1,inplace=True)
df.head()

Name    Location  Year  Kilometers_Driven  \
0            Maruti Wagon R LXI CNG      Mumbai  2010              72000   
1  Hyundai Creta 1.6 CRDi SX Option        Pune  2015              41000   
2                      Honda Jazz V     Chennai  2011              46000   
3                 Maruti Ertiga VDI     Chennai  2012              87000   
4   Audi A4 New 2.0 TDI Multitronic  Coimbatore  2013              40670   

  Fuel_Type Transmission Owner_Type     Mileage   Engine      Power  Seats  \
0       CNG       Manual      First  26.6 km/kg   998 CC  58.16 bhp    5.0   
1    Diesel       Manual      First  19.67 kmpl  1582 CC  126.2 bhp    5.0   
2    Petrol       Manual      First   18.2 kmpl  1199 CC   88.7 bhp    5.0   
3    Diesel       Manual      First  20.77 kmpl  1248 CC  88.76 bhp    7.0   
4    Diesel    Automatic     Second   15.2 kmpl  1968 CC  140.8 bhp    5.0   

   Price  
0   1.75  
1  12.50  
2   4.50  
3   6.00  
4  17.74

> Why did I choose to remove Null values and not to replace it ? 
- That's simply because this columns need to be fixed and we cannot calculate any value before we fix it. 
- another solution is to make a place holder and replace it after fixing data, (Your desicion id depende on the time) 

In [230]:
#fill missing values
df.isna().sum()
df.dropna(inplace=True)
df.isna().sum()

Name                 0
Location             0
Year                 0
Kilometers_Driven    0
Fuel_Type            0
Transmission         0
Owner_Type           0
Mileage              0
Engine               0
Power                0
Seats                0
Price                0
dtype: int64

In [231]:
#strange values
df[df['Power'] == 'null bhp']

Name   Location  Year  \
76                Ford Fiesta 1.4 SXi TDCi     Jaipur  2008   
79                  Hyundai Santro Xing XL  Hyderabad  2005   
89                  Hyundai Santro Xing XO  Hyderabad  2007   
120   Hyundai Santro Xing XL eRLX Euro III     Mumbai  2005   
143    Hyundai Santro Xing XO eRLX Euro II      Kochi  2008   
...                                    ...        ...   ...   
5861                Hyundai Santro Xing XO    Chennai  2007   
5873   Hyundai Santro Xing XO eRLX Euro II       Pune  2006   
5925           Skoda Laura Classic 1.8 TSI       Pune  2010   
5943               Mahindra Jeep MM 540 DP    Chennai  2002   
5985                       Toyota Etios GD      Delhi  2013   

      Kilometers_Driven Fuel_Type Transmission Owner_Type     Mileage  \
76               111111    Diesel       Manual      First   17.8 kmpl   
79                87591    Petrol       Manual      First    0.0 kmpl   
89                73745    Petrol       Manual      First   17.0 kmpl   
120              102000    Petrol       Manual     Second   17.0 kmpl   
143               80759    Petrol       Manual      Third   17.0 kmpl   
...                 ...       ...          ...        ...         ...   
5861              79000    Petrol       Manual      First   17.0 kmpl   
5873              47200    Petrol       Manual     Second   17.0 kmpl   
5925              85000    Petrol       Manual      First   17.5 kmpl   
5943              75000    Diesel       Manual      First    0.0 kmpl   
5985              70000    Diesel       Manual      First  23.59 kmpl   

       Engine     Power  Seats  Price  
76    1399 CC  null bhp    5.0   2.00  
79    1086 CC  null bhp    5.0   1.30  
89    1086 CC  null bhp    5.0   2.10  
120   1086 CC  null bhp    5.0   0.85  
143   1086 CC  null bhp    5.0   1.67  
...       ...       ...    ...    ...  
5861  1086 CC  null bhp    5.0   1.85  
5873  1086 CC  null bhp    5.0   1.20  
5925  1798 CC  null bhp    5.0   2.85  
5943  2112 CC  null bhp    6.0   1.70  
5985  1364 CC  null bhp    5.0   3.88  

[103 rows x 12 columns]

In [232]:
indx=df[df['Power'] == 'null bhp'].index

In [233]:
df.drop(indx,axis=0,inplace=True)

- (KMPL) is refered to Kilometers Per Litre
- (km/kg) is refered to kilometers Per kilogram
> 1 liter  = 1 kilogram 
- Reference : https://en.wikipedia.org/wiki/Litre

In [234]:
#column names
df.columns=df.columns.str.lower().str.strip().str.replace(' ','_')
df.columns


Index(['name', 'location', 'year', 'kilometers_driven', 'fuel_type',
       'transmission', 'owner_type', 'mileage', 'engine', 'power', 'seats',
       'price'],
      dtype='object')

In [235]:
dirty_col=['mileage', 'engine', 'power']
for i in dirty_col :
    df[i]=df[i].apply(lambda x : float(x.split()[0]))    

In [236]:
#clean row
df[df['seats'] == 0] 

Empty DataFrame
Columns: [name, location, year, kilometers_driven, fuel_type, transmission, owner_type, mileage, engine, power, seats, price]
Index: []

In [237]:


#clean column 
df.dtypes
convert_to_int=['engine','seats']
for i in convert_to_int :
    df[i]=df[i].astype(int)
df.dtypes    

name                  object
location              object
year                   int64
kilometers_driven      int64
fuel_type             object
transmission          object
owner_type            object
mileage              float64
engine                 int32
power                float64
seats                  int32
price                float64
dtype: object

#### values health checking 

In [238]:
df.info()
x=100 - ((len(df)/6019) * 100 )
print("loss of data is : ",np.around(x,1),"%")

<class 'pandas.core.frame.DataFrame'>
Int64Index: 5872 entries, 0 to 6018
Data columns (total 12 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   name               5872 non-null   object 
 1   location           5872 non-null   object 
 2   year               5872 non-null   int64  
 3   kilometers_driven  5872 non-null   int64  
 4   fuel_type          5872 non-null   object 
 5   transmission       5872 non-null   object 
 6   owner_type         5872 non-null   object 
 7   mileage            5872 non-null   float64
 8   engine             5872 non-null   int32  
 9   power              5872 non-null   float64
 10  seats              5872 non-null   int32  
 11  price              5872 non-null   float64
dtypes: float64(3), int32(2), int64(2), object(5)
memory usage: 550.5+ KB
loss of data is :  2.4 %


___________________________________

# 2. Feature Engineering

In [239]:
df['name'].nunique()

1811

>  "Name" feature has no affect that's because it has so many unique values 
- So let's make it useful and impactful 

In [240]:
#domain knowledge feature
#get the brand name
def get_brand(x):
    return x.split()[0]
df['brand']=df['name'].apply(get_brand)
#df['brand']=df['name'].apply(lambda x : x.split()[0])
df['brand'].nunique()

30

> We can notice that the first word of the name is (Brand), so let's get it 

In [241]:
#string operation
def get_model(x):
    x_fix=x.split()[2:]
    #convert list to string
    x=" ".join(x_fix)
    return x
df['model_name']=df['name'].apply(get_model)
#df['model_name']=df['name'].apply(lambda x : " ".join(x.split()[2:]))
def fix_name(x):
    x_fix=x.split()[:2]
    #convert list to string
    x=" ".join(x_fix)
    return x
df['name']=df['name'].apply(fix_name)
#df['name']=df['name'].apply(lambda x : " ".join(x.split()[:2]))
df

name    location  year  kilometers_driven fuel_type  \
0       Maruti Wagon      Mumbai  2010              72000       CNG   
1      Hyundai Creta        Pune  2015              41000    Diesel   
2         Honda Jazz     Chennai  2011              46000    Petrol   
3      Maruti Ertiga     Chennai  2012              87000    Diesel   
4            Audi A4  Coimbatore  2013              40670    Diesel   
...              ...         ...   ...                ...       ...   
6014    Maruti Swift       Delhi  2014              27365    Diesel   
6015   Hyundai Xcent      Jaipur  2015             100000    Diesel   
6016   Mahindra Xylo      Jaipur  2012              55000    Diesel   
6017    Maruti Wagon     Kolkata  2013              46000    Petrol   
6018  Chevrolet Beat   Hyderabad  2011              47000    Diesel   

     transmission owner_type  mileage  engine   power  seats  price  \
0          Manual      First    26.60     998   58.16      5   1.75   
1          Manual      First    19.67    1582  126.20      5  12.50   
2          Manual      First    18.20    1199   88.70      5   4.50   
3          Manual      First    20.77    1248   88.76      7   6.00   
4       Automatic     Second    15.20    1968  140.80      5  17.74   
...           ...        ...      ...     ...     ...    ...    ...   
6014       Manual      First    28.40    1248   74.00      5   4.75   
6015       Manual      First    24.40    1120   71.00      5   4.00   
6016       Manual     Second    14.00    2498  112.00      8   2.90   
6017       Manual      First    18.90     998   67.10      5   2.65   
6018       Manual      First    25.44     936   57.60      5   2.50   

          brand               model_name  
0        Maruti                R LXI CNG  
1       Hyundai       1.6 CRDi SX Option  
2         Honda                        V  
3        Maruti                      VDI  
4          Audi  New 2.0 TDI Multitronic  
...         ...                      ...  
6014     Maruti                      VDI  
6015    Hyundai               1.1 CRDi S  
6016   Mahindra                  D4 BSIV  
6017     Maruti                    R VXI  
6018  Chevrolet                   Diesel  

[5872 rows x 14 columns]

In [242]:
df['name'].nunique()

207

- A huge difference here, From this columns we can make a big affect. 

> Another observation that first two word can express wich car we want. 
- So, let's change name column with just first 2 words. 

In [243]:
#we find that model_name column is useless and has redunant inforamtion at another places so we drop it
df.drop('model_name',axis=1,inplace=True)

- That's great, Now we can make an affect with name column. 

________________________

In [244]:
df.sample(5)

name   location  year  kilometers_driven fuel_type  \
4137     Hyundai i10    Kolkata  2012              31000    Petrol   
1985           BMW 3    Chennai  2014              48000    Diesel   
4906  Ford Endeavour  Hyderabad  2018              15000    Diesel   
2819  Hyundai Accent     Mumbai  2005             150000    Diesel   
1726       Ford Figo    Kolkata  2015               1001    Diesel   

     transmission owner_type  mileage  engine  power  seats  price    brand  
4137       Manual      First    20.36    1197   78.9      5   2.25  Hyundai  
1985    Automatic      First    22.69    1995  190.0      5  21.60      BMW  
4906    Automatic      First    10.91    3198  197.0      7  33.00     Ford  
2819       Manual      First    13.10    1493   82.0      5   0.85  Hyundai  
1726       Manual      First    25.83    1498   99.0      5   7.55     Ford

In [245]:
df.reset_index(inplace=True)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5872 entries, 0 to 5871
Data columns (total 14 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   index              5872 non-null   int64  
 1   name               5872 non-null   object 
 2   location           5872 non-null   object 
 3   year               5872 non-null   int64  
 4   kilometers_driven  5872 non-null   int64  
 5   fuel_type          5872 non-null   object 
 6   transmission       5872 non-null   object 
 7   owner_type         5872 non-null   object 
 8   mileage            5872 non-null   float64
 9   engine             5872 non-null   int32  
 10  power              5872 non-null   float64
 11  seats              5872 non-null   int32  
 12  price              5872 non-null   float64
 13  brand              5872 non-null   object 
dtypes: float64(3), int32(2), int64(3), object(6)
memory usage: 596.5+ KB


________________________

# 3. Data understanding 

### 3.1 Univariate analysis 

In [246]:
df.columns
df.drop('index',axis=1,inplace=True)
df.columns

Index(['name', 'location', 'year', 'kilometers_driven', 'fuel_type',
       'transmission', 'owner_type', 'mileage', 'engine', 'power', 'seats',
       'price', 'brand'],
      dtype='object')

In [247]:
#univariate analysis
lst=['year', 'kilometers_driven', 'fuel_type',
       'transmission','seats','brand','owner_type','location']
for i in lst :
    print(f'for feature {i} : \n',df[i].value_counts())
    print()
    fig=px.histogram(df,i,title=f'{i}',color_discrete_sequence=['green'],marginal='box',text_auto=True)
    fig.update_layout(title_x=0.5)
    fig.show()
    print("-------------------------------------------------------------------------------")

for feature year : 
 2014    794
2015    740
2016    737
2013    639
2017    586
2012    562
2011    452
2010    333
2018    298
2009    191
2008    162
2007    105
2019    102
2006     66
2005     42
2004     25
2003     14
2002     11
2000      4
2001      4
1998      3
1999      2
Name: year, dtype: int64



-------------------------------------------------------------------------------
for feature kilometers_driven : 
 60000    80
45000    69
65000    67
50000    60
55000    58
         ..
28937     1
82085     1
68465     1
63854     1
27365     1
Name: kilometers_driven, Length: 3038, dtype: int64



-------------------------------------------------------------------------------
for feature fuel_type : 
 Diesel    3152
Petrol    2655
CNG         55
LPG         10
Name: fuel_type, dtype: int64



-------------------------------------------------------------------------------
for feature transmission : 
 Manual       4170
Automatic    1702
Name: transmission, dtype: int64



-------------------------------------------------------------------------------
for feature seats : 
 5     4919
7      672
8      133
4       99
6       29
2       13
10       4
9        3
Name: seats, dtype: int64



-------------------------------------------------------------------------------
for feature brand : 
 Maruti           1175
Hyundai          1058
Honda             600
Toyota            394
Mercedes-Benz     316
Volkswagen        314
Ford              294
Mahindra          268
BMW               262
Audi              235
Tata              183
Skoda             172
Renault           145
Chevrolet         120
Nissan             89
Land               57
Jaguar             40
Mitsubishi         27
Mini               26
Fiat               23
Volvo              21
Porsche            16
Jeep               15
Datsun             13
Force               3
ISUZU               2
Ambassador          1
Isuzu               1
Bentley             1
Lamborghini         1
Name: brand, dtype: int64



-------------------------------------------------------------------------------
for feature owner_type : 
 First             4839
Second             925
Third              101
Fourth & Above       7
Name: owner_type, dtype: int64



-------------------------------------------------------------------------------
for feature location : 
 Mumbai        775
Hyderabad     718
Kochi         645
Coimbatore    629
Pune          594
Delhi         545
Kolkata       521
Chennai       476
Jaipur        402
Bangalore     347
Ahmedabad     220
Name: location, dtype: int64



-------------------------------------------------------------------------------


In [248]:
#bivaraite analysis
lst=['year', 'kilometers_driven', 'fuel_type',
       'transmission','brand']

In [249]:
for i in range(len(lst)):
    for j in range(i+1,len(lst)):
        fig=px.scatter(df,x=lst[i],y=lst[j],color_discrete_sequence=['pink'],title=f'for feature {lst[i]} vs feature {lst[j]} ')
        fig.update_layout(title_x=0.5)
        fig.show() 
        print("-------------------------------------------------------------------------------")

-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


# Remove Outliers to check data distribution 

In [250]:
#detect and handle outliers
#detect
lst=[]
for i in df.columns:
    #if df[i].select_dtypes('number) : 
    if df[i].dtypes == 'int64' or df[i].dtypes == 'float64' or df[i].dtypes == 'int32' or df[i].dtypes == 'float32' :
        lst.append(i)
print(lst)

['year', 'kilometers_driven', 'mileage', 'engine', 'power', 'seats', 'price']


In [251]:
lst.remove('year')
lst

['kilometers_driven', 'mileage', 'engine', 'power', 'seats', 'price']

In [252]:
#handle
outliers = detect_outliers(df,0,lst)
df.drop(outliers,axis=0,inplace=True)

In [253]:
for i in lst :
    fig=px.histogram(df,i,title=f'{i}',color_discrete_sequence=['green'],marginal='box',text_auto=True)
    fig.update_layout(title_x=0.5)
    fig.show()
    print("-------------------------------------------------------------------------------")

-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


-------------------------------------------------------------------------------


In [254]:
df.reset_index(inplace=True)
df

index            name    location  year  kilometers_driven fuel_type  \
0         0    Maruti Wagon      Mumbai  2010              72000       CNG   
1         1   Hyundai Creta        Pune  2015              41000    Diesel   
2         2      Honda Jazz     Chennai  2011              46000    Petrol   
3         4         Audi A4  Coimbatore  2013              40670    Diesel   
4         5     Hyundai EON   Hyderabad  2012              75000       LPG   
...     ...             ...         ...   ...                ...       ...   
4237   5866     Honda Amaze  Coimbatore  2015              70602    Diesel   
4238   5867    Maruti Swift       Delhi  2014              27365    Diesel   
4239   5868   Hyundai Xcent      Jaipur  2015             100000    Diesel   
4240   5870    Maruti Wagon     Kolkata  2013              46000    Petrol   
4241   5871  Chevrolet Beat   Hyderabad  2011              47000    Diesel   

     transmission owner_type  mileage  engine   power  seats  price      brand  
0          Manual      First    26.60     998   58.16      5   1.75     Maruti  
1          Manual      First    19.67    1582  126.20      5  12.50    Hyundai  
2          Manual      First    18.20    1199   88.70      5   4.50      Honda  
3       Automatic     Second    15.20    1968  140.80      5  17.74       Audi  
4          Manual      First    21.10     814   55.20      5   2.35    Hyundai  
...           ...        ...      ...     ...     ...    ...    ...        ...  
4237       Manual      First    25.80    1498   98.60      5   4.83      Honda  
4238       Manual      First    28.40    1248   74.00      5   4.75     Maruti  
4239       Manual      First    24.40    1120   71.00      5   4.00    Hyundai  
4240       Manual      First    18.90     998   67.10      5   2.65     Maruti  
4241       Manual      First    25.44     936   57.60      5   2.50  Chevrolet  

[4242 rows x 14 columns]

In [255]:
df.drop('index',axis=1,inplace=True)

In [256]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4242 entries, 0 to 4241
Data columns (total 13 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   name               4242 non-null   object 
 1   location           4242 non-null   object 
 2   year               4242 non-null   int64  
 3   kilometers_driven  4242 non-null   int64  
 4   fuel_type          4242 non-null   object 
 5   transmission       4242 non-null   object 
 6   owner_type         4242 non-null   object 
 7   mileage            4242 non-null   float64
 8   engine             4242 non-null   int32  
 9   power              4242 non-null   float64
 10  seats              4242 non-null   int32  
 11  price              4242 non-null   float64
 12  brand              4242 non-null   object 
dtypes: float64(3), int32(2), int64(2), object(6)
memory usage: 397.8+ KB


In [257]:
x=100 - ((len(df)/5871) * 100 )
print("loss of data is : ",np.around(x,1),"%")

loss of data is :  27.7 %


In [258]:
df.describe(include="all")

name location         year  kilometers_driven fuel_type  \
count           4242     4242  4242.000000        4242.000000      4242   
unique           134       11          NaN                NaN         4   
top     Maruti Swift   Mumbai          NaN                NaN    Petrol   
freq             315      579          NaN                NaN      2418   
mean             NaN      NaN  2013.363979       52929.574022       NaN   
std              NaN      NaN     3.149277       26279.502173       NaN   
min              NaN      NaN  1998.000000         171.000000       NaN   
25%              NaN      NaN  2011.000000       33000.000000       NaN   
50%              NaN      NaN  2014.000000       52000.000000       NaN   
75%              NaN      NaN  2016.000000       70000.000000       NaN   
max              NaN      NaN  2019.000000      130002.000000       NaN   

       transmission owner_type      mileage       engine        power   seats  \
count          4242       4242  4242.000000  4242.000000  4242.000000  4242.0   
unique            2          4          NaN          NaN          NaN     NaN   
top          Manual      First          NaN          NaN          NaN     NaN   
freq           3386       3499          NaN          NaN          NaN     NaN   
mean            NaN        NaN    19.423946  1392.026874    95.964114     5.0   
std             NaN        NaN     3.745941   347.653853    33.255344     0.0   
min             NaN        NaN     8.700000   793.000000    34.200000     5.0   
25%             NaN        NaN    17.000000  1197.000000    73.970000     5.0   
50%             NaN        NaN    19.080000  1298.000000    86.775000     5.0   
75%             NaN        NaN    22.100000  1498.000000   110.000000     5.0   
max             NaN        NaN    28.400000  2997.000000   231.100000     5.0   

              price   brand  
count   4242.000000    4242  
unique          NaN      24  
top             NaN  Maruti  
freq            NaN    1035  
mean       5.721306     NaN  
std        3.636650     NaN  
min        0.450000     NaN  
25%        3.250000     NaN  
50%        4.800000     NaN  
75%        6.957500     NaN  
max       19.500000     NaN

### 3.2 Univariate analysis 

- year
- kilometers 
- transmission 
- brand 

## Data summery : 
    - Numerical columns follow the gussian distribution, but have Outliers 
    (My desicion is not to remove it,because it will ne useful)
    - The countrt with the most sales spread is `Mumbai` and the least is `Ahmedabad`
    - Most of cars is form 2010 and 2015

In [259]:
df.sample(5)

name    location  year  kilometers_driven fuel_type  \
2090  Volkswagen Polo  Coimbatore  2015              29651    Petrol   
2895       Honda City  Coimbatore  2012              77283    Petrol   
184     Ford EcoSport      Mumbai  2017              22695    Petrol   
928     Hyundai Grand       Kochi  2019              18453    Petrol   
1906      Hyundai i20   Hyderabad  2017              14061    Diesel   

     transmission owner_type  mileage  engine   power  seats  price  \
2090       Manual      First    16.47    1198   74.00      5   6.43   
2895       Manual      First    17.00    1497  118.00      5   5.81   
184        Manual      First    18.88     999  123.24      5   8.50   
928        Manual      First    18.90    1197   81.86      5   6.17   
1906       Manual      First    21.90    1396   88.76      5   7.40   

           brand  
2090  Volkswagen  
2895       Honda  
184         Ford  
928      Hyundai  
1906     Hyundai

________________________

# 4. Data pre-processing

### 4.1 Data splitting 

In [271]:
#split data
df_copy=df
x=df_copy.drop('price',axis=1)
y=df_copy['price']
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.25, random_state=1)

In [272]:
x_train

name    location  year  kilometers_driven fuel_type  \
2558  Volkswagen Vento   Hyderabad  2010              71000    Diesel   
1690     Ford EcoSport      Mumbai  2017              30000    Diesel   
1322      Maruti Dzire       Delhi  2016              45376    Diesel   
4          Hyundai EON   Hyderabad  2012              75000       LPG   
2975    Renault Duster   Hyderabad  2015              63000    Diesel   
...                ...         ...   ...                ...       ...   
2895        Honda City  Coimbatore  2012              77283    Petrol   
2763       Maruti Alto        Pune  2016               7000    Petrol   
905         Honda City       Kochi  2016              54317    Petrol   
3980       Hyundai i20       Kochi  2014              42315    Petrol   
235      Skoda Octavia      Jaipur  2005             100000    Petrol   

     transmission owner_type  mileage  engine   power  seats       brand  
2558       Manual      First    20.54    1598  103.60      5  Volkswagen  
1690       Manual      First    23.00    1498   98.96      5        Ford  
1322       Manual      First    28.40    1248   73.75      5      Maruti  
4          Manual      First    21.10     814   55.20      5     Hyundai  
2975       Manual     Second    19.72    1461  108.45      5     Renault  
...           ...        ...      ...     ...     ...    ...         ...  
2895       Manual      First    17.00    1497  118.00      5       Honda  
2763       Manual      First    24.07     998   67.10      5      Maruti  
905        Manual      First    17.40    1497  117.30      5       Honda  
3980       Manual      First    18.50    1197   82.90      5     Hyundai  
235     Automatic      First    14.45    1984  227.00      5       Skoda  

[3181 rows x 12 columns]

In [273]:
x_test

name    location  year  kilometers_driven fuel_type  \
3138          Hyundai Elite       Kochi  2016              56911    Petrol   
2753             Honda City   Hyderabad  2017              12538    Petrol   
486              Honda Jazz       Kochi  2018              20024    Petrol   
1050          Hyundai Creta       Delhi  2016              68000    Petrol   
2925          Hyundai Creta   Hyderabad  2015              48200    Petrol   
...                     ...         ...   ...                ...       ...   
267             Maruti Alto      Jaipur  2010             125000    Petrol   
1140             Honda Brio      Jaipur  2013              53959    Petrol   
689            Maruti Swift  Coimbatore  2013              61110    Petrol   
60              Hyundai i10        Pune  2009              95980    Petrol   
3242  Mercedes-Benz E-Class      Mumbai  2011              55000    Diesel   

     transmission owner_type  mileage  engine   power  seats          brand  
3138       Manual      First    18.60    1197   81.86      5        Hyundai  
2753    Automatic      First    18.00    1497  117.30      5          Honda  
486        Manual      First    18.20    1199   88.70      5          Honda  
1050       Manual      First    15.29    1591  121.30      5        Hyundai  
2925       Manual      First    15.29    1591  121.30      5        Hyundai  
...           ...        ...      ...     ...     ...    ...            ...  
267        Manual      First    19.70     796   46.30      5         Maruti  
1140       Manual      First    19.40    1198   86.80      5          Honda  
689        Manual      First    18.60    1197   85.80      5         Maruti  
60         Manual      First    20.36    1197   78.90      5        Hyundai  
3242    Automatic     Second    14.21    2143  203.00      5  Mercedes-Benz  

[1061 rows x 12 columns]

> Why I have started with splliting data  ?
- That's to avoid data leakage problem. 

### 4.2 Data transformation 

#### 4.2.1 Numerical transformation 

In [274]:
#data transformation
#work with numeric
lst_num=[]
for i in x_train.columns:
    if x_train[i].dtypes == 'int64' or x_train[i].dtypes == 'float64' or x_train[i].dtypes == 'int32' or x_train[i].dtypes == 'float32' :
        lst_num.append(i)
print(lst_num)

['year', 'kilometers_driven', 'mileage', 'engine', 'power', 'seats']


In [275]:
#define robust scaler object
scaler=RobustScaler()
#fit on the training dataset
scaler.fit(x_train[lst_num])
#scale the training dataset
x_train[lst_num]=scaler.transform(x_train[lst_num])
#scale the test dataset
x_test[lst_num]=scaler.transform(x_test[lst_num])

In [276]:
x_train

name    location  year  kilometers_driven fuel_type  \
2558  Volkswagen Vento   Hyderabad  -0.8           0.515073    Diesel   
1690     Ford EcoSport      Mumbai   0.6          -0.596400    Diesel   
1322      Maruti Dzire       Delhi   0.4          -0.179571    Diesel   
4          Hyundai EON   Hyderabad  -0.4           0.623509       LPG   
2975    Renault Duster   Hyderabad   0.2           0.298200    Diesel   
...                ...         ...   ...                ...       ...   
2895        Honda City  Coimbatore  -0.4           0.685399    Petrol   
2763       Maruti Alto        Pune   0.4          -1.219909    Petrol   
905         Honda City       Kochi   0.4           0.062812    Petrol   
3980       Hyundai i20       Kochi   0.0          -0.262552    Petrol   
235      Skoda Octavia      Jaipur  -1.8           1.301236    Petrol   

     transmission owner_type   mileage    engine     power  seats       brand  
2558       Manual      First  0.301775  0.779221  0.437500    0.0  Volkswagen  
1690       Manual      First  0.786982  0.519481  0.316667    0.0        Ford  
1322       Manual      First  1.852071 -0.129870 -0.339844    0.0      Maruti  
4          Manual      First  0.412229 -1.257143 -0.822917    0.0     Hyundai  
2975       Manual     Second  0.140039  0.423377  0.563802    0.0     Renault  
...           ...        ...       ...       ...       ...    ...         ...  
2895       Manual      First -0.396450  0.516883  0.812500    0.0       Honda  
2763       Manual      First  0.998028 -0.779221 -0.513021    0.0      Maruti  
905        Manual      First -0.317554  0.516883  0.794271    0.0       Honda  
3980       Manual      First -0.100592 -0.262338 -0.101562    0.0     Hyundai  
235     Automatic      First -0.899408  1.781818  3.651042    0.0       Skoda  

[3181 rows x 12 columns]

In [277]:
x_test

name    location  year  kilometers_driven fuel_type  \
3138          Hyundai Elite       Kochi   0.4           0.133133    Petrol   
2753             Honda City   Hyderabad   0.6          -1.069779    Petrol   
486              Honda Jazz       Kochi   0.8          -0.866840    Petrol   
1050          Hyundai Creta       Delhi   0.4           0.433745    Petrol   
2925          Hyundai Creta   Hyderabad   0.2          -0.103015    Petrol   
...                     ...         ...   ...                ...       ...   
267             Maruti Alto      Jaipur  -0.8           1.978963    Petrol   
1140             Honda Brio      Jaipur  -0.2           0.053107    Petrol   
689            Maruti Swift  Coimbatore  -0.2           0.246964    Petrol   
60              Hyundai i10        Pune  -1.0           1.192258    Petrol   
3242  Mercedes-Benz E-Class      Mumbai  -0.6           0.081327    Diesel   

     transmission owner_type   mileage    engine     power  seats  \
3138       Manual      First -0.080868 -0.262338 -0.128646    0.0   
2753    Automatic      First -0.199211  0.516883  0.794271    0.0   
486        Manual      First -0.159763 -0.257143  0.049479    0.0   
1050       Manual      First -0.733728  0.761039  0.898437    0.0   
2925       Manual      First -0.733728  0.761039  0.898437    0.0   
...           ...        ...       ...       ...       ...    ...   
267        Manual      First  0.136095 -1.303896 -1.054687    0.0   
1140       Manual      First  0.076923 -0.259740  0.000000    0.0   
689        Manual      First -0.080868 -0.262338 -0.026042    0.0   
60         Manual      First  0.266272 -0.262338 -0.205729    0.0   
3242    Automatic     Second -0.946746  2.194805  3.026042    0.0   

              brand  
3138        Hyundai  
2753          Honda  
486           Honda  
1050        Hyundai  
2925        Hyundai  
...             ...  
267          Maruti  
1140          Honda  
689          Maruti  
60          Hyundai  
3242  Mercedes-Benz  

[1061 rows x 12 columns]

In [278]:
x_train.columns

Index(['name', 'location', 'year', 'kilometers_driven', 'fuel_type',
       'transmission', 'owner_type', 'mileage', 'engine', 'power', 'seats',
       'brand'],
      dtype='object')

#### 4.2.1 Catogerical transformation

In [ ]:
#work with categorical

##### 4.2.1.1 ordinal transformation

> The best case of owner type is (First), Of course the worst is Fourth & Above

In [279]:
#work with ordinal
lst_ord=['owner_type']
x_train['owner_type'].value_counts()

First             2635
Second             491
Third               53
Fourth & Above       2
Name: owner_type, dtype: int64

In [280]:
dic={
 'Fourth & Above' : 0 ,
 'Third' : 1 ,
 'Second' : 2 ,   
 'First' : 3 ,       
}


In [281]:
x_train['owner_type']=x_train['owner_type'].map(dic)

In [282]:
x_test['owner_type']=x_test['owner_type'].map(dic)

In [284]:
x_train

name    location  year  kilometers_driven fuel_type  \
2558  Volkswagen Vento   Hyderabad  -0.8           0.515073    Diesel   
1690     Ford EcoSport      Mumbai   0.6          -0.596400    Diesel   
1322      Maruti Dzire       Delhi   0.4          -0.179571    Diesel   
4          Hyundai EON   Hyderabad  -0.4           0.623509       LPG   
2975    Renault Duster   Hyderabad   0.2           0.298200    Diesel   
...                ...         ...   ...                ...       ...   
2895        Honda City  Coimbatore  -0.4           0.685399    Petrol   
2763       Maruti Alto        Pune   0.4          -1.219909    Petrol   
905         Honda City       Kochi   0.4           0.062812    Petrol   
3980       Hyundai i20       Kochi   0.0          -0.262552    Petrol   
235      Skoda Octavia      Jaipur  -1.8           1.301236    Petrol   

     transmission  owner_type   mileage    engine     power  seats       brand  
2558       Manual           3  0.301775  0.779221  0.437500    0.0  Volkswagen  
1690       Manual           3  0.786982  0.519481  0.316667    0.0        Ford  
1322       Manual           3  1.852071 -0.129870 -0.339844    0.0      Maruti  
4          Manual           3  0.412229 -1.257143 -0.822917    0.0     Hyundai  
2975       Manual           2  0.140039  0.423377  0.563802    0.0     Renault  
...           ...         ...       ...       ...       ...    ...         ...  
2895       Manual           3 -0.396450  0.516883  0.812500    0.0       Honda  
2763       Manual           3  0.998028 -0.779221 -0.513021    0.0      Maruti  
905        Manual           3 -0.317554  0.516883  0.794271    0.0       Honda  
3980       Manual           3 -0.100592 -0.262338 -0.101562    0.0     Hyundai  
235     Automatic           3 -0.899408  1.781818  3.651042    0.0       Skoda  

[3181 rows x 12 columns]

In [285]:
x_test

name    location  year  kilometers_driven fuel_type  \
3138          Hyundai Elite       Kochi   0.4           0.133133    Petrol   
2753             Honda City   Hyderabad   0.6          -1.069779    Petrol   
486              Honda Jazz       Kochi   0.8          -0.866840    Petrol   
1050          Hyundai Creta       Delhi   0.4           0.433745    Petrol   
2925          Hyundai Creta   Hyderabad   0.2          -0.103015    Petrol   
...                     ...         ...   ...                ...       ...   
267             Maruti Alto      Jaipur  -0.8           1.978963    Petrol   
1140             Honda Brio      Jaipur  -0.2           0.053107    Petrol   
689            Maruti Swift  Coimbatore  -0.2           0.246964    Petrol   
60              Hyundai i10        Pune  -1.0           1.192258    Petrol   
3242  Mercedes-Benz E-Class      Mumbai  -0.6           0.081327    Diesel   

     transmission  owner_type   mileage    engine     power  seats  \
3138       Manual           3 -0.080868 -0.262338 -0.128646    0.0   
2753    Automatic           3 -0.199211  0.516883  0.794271    0.0   
486        Manual           3 -0.159763 -0.257143  0.049479    0.0   
1050       Manual           3 -0.733728  0.761039  0.898437    0.0   
2925       Manual           3 -0.733728  0.761039  0.898437    0.0   
...           ...         ...       ...       ...       ...    ...   
267        Manual           3  0.136095 -1.303896 -1.054687    0.0   
1140       Manual           3  0.076923 -0.259740  0.000000    0.0   
689        Manual           3 -0.080868 -0.262338 -0.026042    0.0   
60         Manual           3  0.266272 -0.262338 -0.205729    0.0   
3242    Automatic           2 -0.946746  2.194805  3.026042    0.0   

              brand  
3138        Hyundai  
2753          Honda  
486           Honda  
1050        Hyundai  
2925        Hyundai  
...             ...  
267          Maruti  
1140          Honda  
689          Maruti  
60          Hyundai  
3242  Mercedes-Benz  

[1061 rows x 12 columns]

##### 4.2.1.2 Nominal transformation


In [286]:
#work with nomial data
lst_nom=[]
for i in x_train.columns:
    if x_train[i].dtype == 'O':
        lst_nom.append(i)
print(lst_nom)        

['name', 'location', 'fuel_type', 'transmission', 'brand']


In [287]:
for i in lst_nom :
    print(f"for feature {i} : \n",x_train[i].value_counts())
    print()
    print("------------------------------------------")


for feature name : 
 Maruti Swift         231
Honda City           186
Hyundai i20          184
Hyundai Verna        123
Hyundai Grand        117
                    ... 
Ford Classic           1
Mitsubishi Lancer      1
Mini Cooper            1
Datsun Redi            1
Maruti Esteem          1
Name: name, Length: 130, dtype: int64

------------------------------------------
for feature location : 
 Mumbai        437
Hyderabad     388
Kochi         359
Kolkata       336
Pune          324
Coimbatore    284
Delhi         278
Chennai       259
Jaipur        232
Bangalore     157
Ahmedabad     127
Name: location, dtype: int64

------------------------------------------
for feature fuel_type : 
 Petrol    1808
Diesel    1337
CNG         30
LPG          6
Name: fuel_type, dtype: int64

------------------------------------------
for feature transmission : 
 Manual       2522
Automatic     659
Name: transmission, dtype: int64

------------------------------------------
for feature brand : 
 Ma

In [288]:
#binary encoding
binaryencoder = ce.BinaryEncoder(cols=lst_nom)
binaryencoder.fit(x_train)

BinaryEncoder(cols=['name', 'location', 'fuel_type', 'transmission', 'brand'],
              mapping=[{'col': 'name',
                        'mapping':       name_0  name_1  name_2  name_3  name_4  name_5  name_6  name_7
 1         0       0       0       0       0       0       0       1
 2         0       0       0       0       0       0       1       0
 3         0       0       0       0       0       0       1       1
 4         0       0       0       0       0       1       0       0
 5         0       0       0       0       0       1       0       1
...      ...     ...     ...     ...     ...     ...     ...     ...
 128       1       0       0       0       0       0       0       0
 129       1       0       0       0       0       0       0       1
 130       1       0       0       0       0       0       1       0
-1         0       0       0       0       0       0       0       0
-2         0       0       0       0       0       0       0       0

[132 rows x 8 colu

In [289]:
x_train=binaryencoder.transform(x_train)

In [290]:
x_test=binaryencoder.transform(x_test)

# 5.0 Modeling 

### 5.1 Linear regression (OLS method)

In [291]:
x_train

name_0  name_1  name_2  name_3  name_4  name_5  name_6  name_7  \
2558       0       0       0       0       0       0       0       1   
1690       0       0       0       0       0       0       1       0   
1322       0       0       0       0       0       0       1       1   
4          0       0       0       0       0       1       0       0   
2975       0       0       0       0       0       1       0       1   
...      ...     ...     ...     ...     ...     ...     ...     ...   
2895       0       0       0       1       1       1       0       0   
2763       0       0       0       1       1       0       1       1   
905        0       0       0       1       1       1       0       0   
3980       0       0       0       0       0       1       1       1   
235        0       0       1       1       0       1       1       0   

      location_0  location_1  ...  owner_type   mileage    engine     power  \
2558           0           0  ...           3  0.301775  0.779221  0.437500   
1690           0           0  ...           3  0.786982  0.519481  0.316667   
1322           0           0  ...           3  1.852071 -0.129870 -0.339844   
4              0           0  ...           3  0.412229 -1.257143 -0.822917   
2975           0           0  ...           2  0.140039  0.423377  0.563802   
...          ...         ...  ...         ...       ...       ...       ...   
2895           0           1  ...           3 -0.396450  0.516883  0.812500   
2763           0           1  ...           3  0.998028 -0.779221 -0.513021   
905            1           0  ...           3 -0.317554  0.516883  0.794271   
3980           1           0  ...           3 -0.100592 -0.262338 -0.101562   
235            0           1  ...           3 -0.899408  1.781818  3.651042   

      seats  brand_0  brand_1  brand_2  brand_3  brand_4  
2558    0.0        0        0        0        0        1  
1690    0.0        0        0        0        1        0  
1322    0.0        0        0        0        1        1  
4       0.0        0        0        1        0        0  
2975    0.0        0        0        1        0        1  
...     ...      ...      ...      ...      ...      ...  
2895    0.0        0        1        0        0        0  
2763    0.0        0        0        0        1        1  
905     0.0        0        1        0        0        0  
3980    0.0        0        0        1        0        0  
235     0.0        0        1        0        1        0  

[3181 rows x 29 columns]

In [292]:
x_test

name_0  name_1  name_2  name_3  name_4  name_5  name_6  name_7  \
3138       0       1       1       0       1       0       1       0   
2753       0       0       0       1       1       1       0       0   
486        0       0       0       1       0       0       0       0   
1050       0       0       1       1       1       0       0       0   
2925       0       0       1       1       1       0       0       0   
...      ...     ...     ...     ...     ...     ...     ...     ...   
267        0       0       0       1       1       0       1       1   
1140       0       0       1       1       0       0       0       1   
689        0       0       0       0       1       1       1       0   
60         0       0       1       0       1       1       1       1   
3242       0       0       1       1       1       1       1       1   

      location_0  location_1  ...  owner_type   mileage    engine     power  \
3138           1           0  ...           3 -0.080868 -0.262338 -0.128646   
2753           0           0  ...           3 -0.199211  0.516883  0.794271   
486            1           0  ...           3 -0.159763 -0.257143  0.049479   
1050           0           0  ...           3 -0.733728  0.761039  0.898437   
2925           0           0  ...           3 -0.733728  0.761039  0.898437   
...          ...         ...  ...         ...       ...       ...       ...   
267            0           1  ...           3  0.136095 -1.303896 -1.054687   
1140           0           1  ...           3  0.076923 -0.259740  0.000000   
689            0           1  ...           3 -0.080868 -0.262338 -0.026042   
60             0           1  ...           3  0.266272 -0.262338 -0.205729   
3242           0           0  ...           2 -0.946746  2.194805  3.026042   

      seats  brand_0  brand_1  brand_2  brand_3  brand_4  
3138    0.0        0        0        1        0        0  
2753    0.0        0        1        0        0        0  
486     0.0        0        1        0        0        0  
1050    0.0        0        0        1        0        0  
2925    0.0        0        0        1        0        0  
...     ...      ...      ...      ...      ...      ...  
267     0.0        0        0        0        1        1  
1140    0.0        0        1        0        0        0  
689     0.0        0        0        0        1        1  
60      0.0        0        0        1        0        0  
3242    0.0        0        1        1        1        0  

[1061 rows x 29 columns]

In [293]:
#modeling and evaluation
#modeling
#create linear regression object then fit
reg = LinearRegression(n_jobs=-1).fit(x_train,np.log(y_train))

In [294]:
#evaluation
#score of test set
np.around(reg.score(x_test,  np.log(y_test)),2)

0.85

In [295]:
#score of train set
np.around(reg.score(x_train,  np.log(y_train)),2)

0.85

In [296]:
y=reg.predict(x_test)

In [311]:
y
predict_price=pd.DataFrame((y),columns=['Price'])
predict_price
x_pred=pd.concat([x_test,predict_price],axis=1)
x_pred
x_pred.dropna(inplace=True)
x_pred.reset_index(inplace=True)
x_pred.drop('index',axis=1,inplace=True)
x_pred

name_0  name_1  name_2  name_3  name_4  name_5  name_6  name_7  \
0       0.0     0.0     0.0     1.0     0.0     0.0     0.0     0.0   
1       0.0     0.0     1.0     1.0     1.0     0.0     0.0     0.0   
2       0.0     0.0     0.0     0.0     1.0     1.0     0.0     0.0   
3       0.0     0.0     0.0     1.0     1.0     0.0     0.0     0.0   
4       0.0     1.0     0.0     1.0     1.0     0.0     1.0     1.0   
..      ...     ...     ...     ...     ...     ...     ...     ...   
258     0.0     0.0     1.0     0.0     0.0     0.0     1.0     1.0   
259     0.0     0.0     0.0     1.0     1.0     1.0     0.0     0.0   
260     0.0     0.0     0.0     1.0     1.0     0.0     1.0     1.0   
261     0.0     0.0     0.0     0.0     1.0     1.0     1.0     0.0   
262     0.0     0.0     1.0     0.0     1.0     1.0     1.0     1.0   

     location_0  location_1  ...   mileage    engine     power  seats  \
0           1.0         0.0  ... -0.159763 -0.257143  0.049479    0.0   
1           0.0         0.0  ... -0.733728  0.761039  0.898437    0.0   
2           1.0         0.0  ...  0.096647 -0.257143  0.051042    0.0   
3           1.0         0.0  ...  0.802761  0.423377 -0.617187    0.0   
4           0.0         0.0  ... -0.909270  0.254545 -0.567708    0.0   
..          ...         ...  ...       ...       ...       ...    ...   
258         0.0         1.0  ...  0.518738  0.423377 -0.052083    0.0   
259         0.0         0.0  ...  1.378698  0.519481  0.307292    0.0   
260         0.0         1.0  ...  0.136095 -1.303896 -1.054687    0.0   
261         0.0         1.0  ... -0.080868 -0.262338 -0.026042    0.0   
262         0.0         1.0  ...  0.266272 -0.262338 -0.205729    0.0   

     brand_0  brand_1  brand_2  brand_3  brand_4     Price  
0        0.0      1.0      0.0      0.0      0.0  0.777161  
1        0.0      0.0      1.0      0.0      0.0  1.565063  
2        0.0      1.0      0.0      0.0      0.0  0.652710  
3        0.0      1.0      0.0      1.0      1.0  2.189392  
4        0.0      1.0      0.0      0.0      1.0  2.053558  
..       ...      ...      ...      ...      ...       ...  
258      0.0      1.0      0.0      1.0      1.0  0.940308  
259      0.0      1.0      0.0      0.0      0.0  1.780609  
260      0.0      0.0      0.0      1.0      1.0  0.936798  
261      0.0      0.0      0.0      1.0      1.0  1.461395  
262      0.0      0.0      1.0      0.0      0.0  0.987152  

[263 rows x 30 columns]

In [206]:
reg.coef_

array([-3.34498022e-01, -5.00925327e-02, -3.60901707e-02, -2.57673082e-02,
        8.79795764e-02, -3.42405303e-02, -2.88506477e-02,  9.59045634e-03,
       -1.00273213e-01,  3.06370102e-02, -1.20775893e-01, -1.20374823e-02,
        5.64057398e-01, -6.95456005e-02, -2.33397819e-01, -2.38141143e-01,
        6.78866687e-03, -2.02760283e+11, -2.02760283e+11,  8.12394062e-02,
       -4.00923146e-02,  4.83497353e-02,  3.73987999e-01,  1.24153432e+08,
       -6.63080481e-02, -8.33789707e-02,  4.94846197e-02,  7.34948751e-02,
       -8.08376755e-02])

In [207]:
reg.intercept_

202760283238.51654